In [1]:
import sys
sys.path.append('home.hangyeol.sun/anaconda3/envs/legal')

In [2]:
import re
import requests
from time import sleep
import pandas as pd
import multiprocessing

In [3]:
from urllib import parse
from urllib.request import urlopen, urlretrieve
from bs4 import BeautifulSoup

In [4]:
from pdfminer.pdfinterp import PDFResourceManager, PDFPageInterpreter
from pdfminer.converter import TextConverter
from pdfminer.layout import LAParams
from pdfminer.pdfpage import PDFPage
from io import StringIO

In [4]:
def crawl_view_param(last_idx):
    crawl_view_param_list = []
    pattern = re.compile('[0-9]+')
    for i in range(last_idx):
        parameters = {'pageIndex':str(i+1)}
        r = requests.post("https://www.scourt.go.kr/portal/dcboard/DcNewsListAction.work?gubun=44", data = parameters)
        html = r.text
        soup = BeautifulSoup(html, 'html.parser')
        view_param_list = soup.find_all("td", class_="tit")
        for j in view_param_list:
            vp_dic = {}
            view_param = j.find("a")['onclick']
            result = pattern.findall(view_param)
            vp_dic['seqnum'] = result[0]
            vp_dic['cbub_code'] = result[1]
            crawl_view_param_list.append(vp_dic)
            
    return crawl_view_param_list

In [5]:
crawl_view_param_list = crawl_view_param(2077)

In [8]:
crawl_view_param_list

[{'seqnum': '21060', 'cbub_code': '000413'},
 {'seqnum': '21059', 'cbub_code': '000413'},
 {'seqnum': '21058', 'cbub_code': '000413'},
 {'seqnum': '21057', 'cbub_code': '000413'},
 {'seqnum': '21056', 'cbub_code': '000413'},
 {'seqnum': '21055', 'cbub_code': '000413'},
 {'seqnum': '21054', 'cbub_code': '000211'},
 {'seqnum': '21053', 'cbub_code': '000211'},
 {'seqnum': '21051', 'cbub_code': '000280'},
 {'seqnum': '21050', 'cbub_code': '000240'},
 {'seqnum': '21049', 'cbub_code': '000520'},
 {'seqnum': '21048', 'cbub_code': '000420'},
 {'seqnum': '21047', 'cbub_code': '000420'},
 {'seqnum': '21046', 'cbub_code': '000420'},
 {'seqnum': '21045', 'cbub_code': '000420'},
 {'seqnum': '21044', 'cbub_code': '000420'},
 {'seqnum': '21043', 'cbub_code': '000420'},
 {'seqnum': '21042', 'cbub_code': '000420'},
 {'seqnum': '21041', 'cbub_code': '000420'},
 {'seqnum': '21040', 'cbub_code': '000420'},
 {'seqnum': '21039', 'cbub_code': '000420'},
 {'seqnum': '21038', 'cbub_code': '000420'},
 {'seqnum'

In [54]:
for idx, i in enumerate(crawl_view_param_list):
    if i['seqnum'] == '21051':
        print(idx)

8


In [55]:
parameters = crawl_view_param_list[8]
r = requests.post("https://www.scourt.go.kr/portal/dcboard/DcNewsViewAction.work?gubun=44", data = parameters)
print(r.text)



<!DOCTYPE html PUBLIC "-//W3C//DTD HTML 4.01 Transitional//EN" "http://www.w3.org/TR/html4/loose.dtd">


<html lang="ko">
 <head>
 	










<meta http-equiv="X-UA-Compatible" content="IE=edge,chrome=1">
<meta name="viewport" content="width=device-width, initial-scale=1.0, maximum-scale=3.0, minimum-scale=1.0, user-scalable=yes, target-densitydpi=medium-dpi">
<link rel="shortcut icon" href="/scourt/common/images/favicon.ico" type="image/x-icon" />
<script type="text/javascript" src="/js/portal/jquery-1.8.3.js"></script>
<script type="text/javascript" src="/js/portal/jquery-ui-1.8.21.custom.min.js"></script>
<script type="text/javascript" src="/js/portal/common_old.js" charset="euc-kr"></script>
<script type="text/javascript" src="/js/portal/common.js"></script>
<script type="text/javascript" src="/js/portal/embed.js"></script>

<!-- <link rel="stylesheet" type="text/css" href="/css/jquery.ui.datepicker.css">  -->
<!-- <link rel="stylesheet" type="text/css" href="/css/jquery-ui-1.8.

In [66]:
html = r.text
soup = BeautifulSoup(html, 'html.parser')
pdf_url = soup.find('td', class_='attTxt').find_all('a')[0]['href']
pdf_url

'http://file.scourt.go.kr//AttachDownload?file=1568858313026_105833.pdf&path=003&downFile=2019고단214_판결문_검수완료.pdf'

In [122]:
pdf_url = "http://file.scourt.go.kr//AttachDownload?file=1569201663933_102103.pdf&amp;path=003&amp;downFile=부산가정법원_2019드단205783.pdf"
encode_url = parse.urlparse(pdf_url)
query = parse.parse_qs(encode_url.query)
parse.urlencode(query, doseq=True)
#print(encode_url)
#print(query)
#urlretrieve(pdf_url, "pdf/test2.pdf")

'file=1569201663933_102103.pdf&path=003&downFile=%EB%B6%80%EC%82%B0%EA%B0%80%EC%A0%95%EB%B2%95%EC%9B%90_2019%EB%93%9C%EB%8B%A8205783.pdf'

In [100]:
html = r.text
soup = BeautifulSoup(html, 'html.parser')
soup.find_all(text=re.compile('작성자'))[0].parent.find_next_siblings('td')[0].text
#find_next_siblings('td')

'부산가정법원'

In [101]:
soup.find_all(text=re.compile('작성일'))[0].parent.find_next_siblings('td')[0].text

'2019-09-23'

In [106]:
soup.find('td', class_='attTxt').find('a')['href']

'http://file.scourt.go.kr//AttachDownload?file=1569201663933_102103.pdf&path=003&downFile=부산가정법원_2019드단205783.pdf'

In [110]:
soup.find('td', class_='contArea').text

'\n\n▶ 피고는 병에게 배우자가 있음을 알면서도 병과 부정행위를 함으로써 원고의 부부공동생활을 침해하거나 유지를 방해하고 그에 대한 원고의 배우자로서의 권리를 침해하였으므로, 원고가 입은 정신적 손해를 배상할 책임이 있다.\n이에 대해 피고는, 공동불법행위자인 병이 원고에게 위자료 3,000만원을 지급함으로써 피고의 책임도 면책되었다는 취지로 주장하나, 위자료 액수에 관하여는 사실심 법원이 제반 사정을 참작하여 그 직권에 속하는 재량에 의하여 이를 확정할 수 있는바, 피고가 먼저 원고에게 부정행위 사실을 밝히면서 원고를 조롱하였고, 원고에게 제대로 된 사과조차 하지 않은 점, 이 사건 소송 중에는 오히려 자신이 병에게 속은 피해자라며 원고와 병을 비난하기에만 급급하였던 점 등에 비추어 보면, 원고가 병으로부터 3,000만원을 지급받았더라도 이로써 피고에 대한 원고의 손해배상채권이 전부 변제되어 소멸하였다고 볼 수 없고, 다만 앞서 본 바와 같이 피고가 지급할 위자료 액수를 정함에 있어 참작할 사유가 될 뿐이라고 보아, 원고의 위자료 청구 일부를 인용한 사례.\n'

In [6]:
def save_judge(url, file_name):
    parse_url = parse.urlparse(url)
    query = parse.parse_qs(parse_url.query)
    #file_name = query['downFile']
    encode_url = "http://file.scourt.go.kr//AttachDownload?" + parse.urlencode(query, doseq=True)
    urlretrieve(encode_url, 'pdf/{}.pdf'.format(file_name))
    return encode_url

def extract_tag(title):
    pattern = re.compile('(?<=\[).+?(?=\])')
    tag_list = pattern.findall(title)
    if len(tag_list) > 0:
        tag = tag_list[0]
    else:
        tag = 'None'
    return tag

def crawl_judge(view_param):
    judge_dic = {}
    r = requests.post("https://www.scourt.go.kr/portal/dcboard/DcNewsViewAction.work?gubun=44", data = view_param)
    html = r.text
    soup = BeautifulSoup(html, 'html.parser')
    title = soup.find_all('th', text=re.compile('제목'))[0].find_next_siblings('td')[0].text
    writer = soup.find_all('th', text=re.compile('작성자'))[0].find_next_siblings('td')[0].text
    date = soup.find_all('th', text=re.compile('작성일'))[0].find_next_siblings('td')[0].text
    content = soup.find('td', class_='contArea').text
    judge_dic['title'] = title
    judge_dic['writer'] = writer
    judge_dic['date'] = date
    judge_dic['content'] = content
    judge_dic['seqnum'] = view_param['seqnum']
    judge_dic['tag'] = extract_tag(title)
    '''
    try:
        pdf_url_list = soup.find('td', class_='attTxt').find_all('a')
        if len(pdf_url_list) > 1:
            for idx, pdf_url in enumerate(pdf_url_list):
                file_name = "{}_{}".format(view_param['seqnum'], idx)
                save_judge(pdf_url['href'], file_name)
        else:
            save_judge(pdf_url_list[0]['href'], view_param['seqnum'])
    except:
        pass
    #sleep(1)
    '''
    print(judge_dic['seqnum'], judge_dic['title'])
    return judge_dic

In [7]:
all_judge_list_re = []

with multiprocessing.Pool() as pool:
    ret = pool.map(crawl_judge, crawl_view_param_list)

16700 [형사]2015고단2847 약사법위반
17569 [형사] 엑스터시, 필로폰 밀반입 사건
16265 수원지방법원 2013가합7489
19755 [형사]체포 당시 미란다 원칙을 고지하지 않은 것을 발견, 직권으로 판단하여 원심을 파기하고 공무집행방해 무죄를 선고한 판결(수원지법 2018노371)
21063 [행정] 의료기관을 운영하는 의사가 휴가를 이유로 대진의를 구한 경우에 대진의가 자신이 아닌 운영 의사 명의로 처방전을 발급하였다고 하더라도 그 처방전의 작성 사실을 인식하고 용인하였다고 볼 수 있는 경우가 아니라면 의료법 위반이 아니라고 본 사례(서울행정법원 2018구합82144 판결)
18012 [형사] 교제 시 촬영한 동영상으로 협박하고, SNS에 게시한 사건(인천지방법원 2016고단3233)
18884 [형사] 보이스피싱 수법을 이용하여 피해자의 집에 들어가 현금 1,000만 원을 절취한 사건(춘천지방법원 2017노149)
20627 [행정] 고등학교장의 출석정지처분 등에 대한 무효확인 사건(창원지방법원 2018구단12153호)
20192 [민사] 지부장 선거에서 당선된 이후 선거관리위원회의 당선무효결정이 내려지자, 당선인이 지부장 지위 확인을 구하는 사건 (광주고등법원 2018나21639)
18450 [가사] 혼인관계가 파탄에 이르렀다고 보아 원고의 이혼청구를 인용한 사안(부산가정법원 2016드단1355)
17134 [형사] 검찰 출신 변호사를 사칭하여 여성 피해자로부터 2,000여 만 원을 편취한 피고인에게 징역 2년의 중형을 선고한 사례
19318 [형사] 허위세금계산서교부등의 죄에서의 영리의 목적에 관한 사례 (울산지방법원 2016고합450)
17568 [민사] 사실혼관계 파탄에 따른 손해배상책임
19754 [형사]검사 제출 증거만으로 의료과실을 인정할 수 없고 설령 업무상 과실이 인정된다고 하더라도 업무상 과실과 환자의 사망 사이에 인과관계를 인정할 수 없다고 한 판결(수원지법 2017노6226)
18011 [형사] 체류 기간 연장 목

17126 [형사]2016고단368 상해 등
18442 [형사] 음식점에서 종업원이 깨진 소주잔을 제공했다는 이유로 겁을 주면서 음식대금 청구를 단념하게 한 사례
17560 [2016. 7. 15. 가사] 남편이 부인을 상대로 혼인무효확인 청구의 소를 제기함에 대하여 부인은 남편을 상대로 법률상 부부임을 전제로 이혼의 소를 제기한 사안
   배우자 일방이 혼인신고서를 작성하였더라도 상대방의 동의나 승낙을 얻었거나 상대방에게 혼인의 의사가 존재하고 있었을 때에는 일방이 한 혼인신고도 유효하다고 보아 남편의 혼인무효확인 청구를 기각한 반면, 부인이 청구한 이혼 청구에 따라 부부가 이혼하고 귀책사유 있는 남편은 부인에게 위자료 1,000만 원을 지급하라고 한 사례
21055 [가사] 원고의 이혼 및 위자료 청구를 인용한 사안(2017드단206997)
16257 [형사]제조 공정에서 보조적으로 사용된 물이 공공수역으로 배출되지 않을 것이 명백한 경우, 해당 물을 보관하는 '정반'이 '(폐수)배출시설'에 해당하지 않는다고 본 사례
20619 [민사] 아이패드 판매회사를 상대로 잠금해제를 청구한 사안에서, 원고가 아이패드의 소유자임을 인정하기 부족하다는 이유로 거절한 사례
18004 [민사] 피고차량이 주차된 이면도로상에서 원고차량과 오토바이가 충돌하는 교통사고가 발생한 사안에서, 피고차량으로 인하여 노폭이 줄어들기는 하였으나 원고차량과 오토바이가 충분히 교행할 수 있는 공간이 있었고, 피고 차량이 도로교통법을 위반하여 불법주차된 것으로 볼 만한 입증이 부족하다는 점을 종합하여, 피고 차량의 주차와 교통사고와의 상당인과관계를 부정한 사례
19747 [과태료] 위반자들이 H가 정교사 채용시험에 합격할 수 있도록 유리한 심사기준을 채택해 달라거나 H에게 유리하도록 이미 결정된 심사기준을 변경해달라는 청탁은 청탁금지법 상의 부정청탁에 해당한다고 본 사례(의정부지방법원 2017과101)
18876 [형사] 등록 없이 금전을 대부하면서 연 25%의 이율을 초과하는 이자를 받고 위

20178 [형사] 기업의 대표이사인 피고인이 직원들의 4대 보험료 목적으로 사전공제하여 금전을 임의로 사용하여 업무상 횡령한 사건(울산지방법원2018고단94)
17120 [형사]2015고합374, 378(병합) 성폭력범죄의처벌등에관한특례법위반(강간등상해) 등
17998 [가사] 남편이 이혼 소송 중 제출한 소취하서가 적법하다고 보아 소송종료선언을 한 사안(부산가정법원 2015드합314)
18436 [민사] 택시 승객이 사고 상황을 살피기 위하여 잠시 내린 사이 뒤에서 온 차량이 정차한 택시를 충격함에 따라 승객이 상해를 입은 사건에서 택시 공제사업자의 책임을 인정한 사례
21048 [형사]승용차를 급제동하여 뒤차 탑승자에게 상해를 가한 사안(창원지방법원 2018고단3180)
18870 [행정] 군무원은 국가유공자 등 예우 및 지원에 관한 법률에 정한 공상군경에 해당함에도, 피고는 이와 달리 군무원이 공상군경이 아니라 국가유공자법상 공상공무원에 해당한다는 전제에서 이 사건 처분을 하였으므로, 이 사건 처분은 국가유공자법에 반하여 위법하다고 주장한 사건 (울산지방법원 2017구합5014)
19741 [행정] 사업장 변경 불허 처분 취소 사건(울산지방법원2017구합6765)
17553 [2016. 5. 10.자 민사] 자동차 견인 작업 중 주의의무 위반을 인정하지 않은 판결
16686 [2015. 12. 7.자 가사] 가출한 외국인 여성이 남편에 의해 제기된 이혼소송에서 패소한 뒤 자녀들에 대한 면접교섭을 청구하였으나 위 청구가 기각된 사례
20613 [형사] 산업안전보건법위반, 업무상과실치사 사건 (울산지방법원 2018고단3682)
20177 [형사] 아동복지법위반(아동학대) 사건(울산지방법원2018고단594)
16251 [행정] 외국인인 원고가 근무하는 음식점이 외국음식 전문식당이라는 이유로 체류기간 연장불허 처분을 취소한 사례
19303 [형사] 골프장사업, 모텔사업, 공장분양사업 등을 위한 차용금 명목으로 피해자로부터 합계 7억 원을 편취한 사안 (울산지방

17546 [형사] 공직선거법 위반 사건(전주지방법원 2016고합52)
16244 [행정]2015구합5690 평균임금결정처분취소
20170 [형사] 존속살해미수 사건(울산지방법원2018고합47)
19296 [민사] 화재사건에서 피고들이 건물을 설치·보존함에 있어 사회통념상 일반적으로 요구되는 정도의 방호조치의무 (울산지방법원 2016가합22376)
17990 [행정] 임금피크제 지원금 부지급 결정 취소 사건(수원지방법원 2015구단33398)
17112 [형사]2015고단2772, 3245(병합), 2016고단166(병합) 사기
18428 [민사] 사찰의 금동관음보살상 인도 청구에 관하여 인도를 명한 판결
20605 [형사]입영 거부가 진정한 양심에 의한 것이서 정당한 사유가 있다고 인정한 사건(2017고단149)
19733 [형사] 문재인 대통령이 과거 대통령 비서실장으로 재직할 때 북한 김정일 국방위원장에게 편지를 보냈다며 허위사실을 퍼뜨린 피고인에게 벌금형을 선고한 사례 
(서울북부지방법원 2017고합395)
17545 [전주지방법원 형사] 2016. 7. 6. 선고 2016고단487 성매매알선등행위의처벌에관한법률위반(성매매알선등)
21040 [형사] 7세 아동에게 고함을 치는 등 정서적 학대행위를 한 사안(창원지방법원 2018고단1441)
16678 ○[민사] 갑이 수목식재 계약을 체결하고 을의 토지에 수목을 식재한 후 병이 해당 토지를 경락받은 경우 갑은 병에 대해 식재대금채권에 기한 유치권을 주장할 수 없다고 본 판결
18862 [행정] 전교조 소속 교사에 대한 교육청의 징계처분에 관한 취소소송에서, 공무원연금 개혁 저지를 위한 연가투쟁은 징계사유에 해당하므로 징계처분이 정당하다고 본 사안(대구지방법원 2017. 6. 30.선고 2016구합23242 판결)
20169 [형사] 도로교통법위반(음주운전, 무면허운전) 사건(울산지방법원2018고단611)
19295 [행정] 회식자리에서 만취되어 귀가하던 중 발생한 교통사고로 사망한 공무원이 공무상 부상으로

19288 [행정] 전 대통령의 명예를 훼손한 혐의로 징역형을 받고 파면된 전 국립대 철학과 교수가 제기한 파면 무효 소송에서 징계처분이 징계권의 한계를 일탈하거나 재량권을 남용했다고 볼 수 없어 원고의 청구를 기각한 사례(부산지방법원 2017구합986)
21033 [특허]확인대상발명이 당해 특허발명의 균등관계에 해당하여 당해 특허발명의 권리범위에 포함된다고 본 사례(특허법원 2018허9015)
16236 [형사]2번에 걸쳐 여자 화장실에 몰래 침입하여 옆 칸에서 칸막이 위로 훔쳐본 사건에 대하여 실형 선고한 사례
17104 [형사] 국회의원 지역구 사무실에 난입하여 사람을 인질로 잡아 상해를 가한 피고인에게 징역형을 선고한 판결
17982 [민사] 대여금인지 투자금인지의 여부가 쟁점이 된 사건(인천지방법원 2015가합53496)
18418 [형사] 마트 종업원이 손님의 치마 안을 촬영하려다 발각된 사건 (울산지방법원 2016고단3962)
17537 [형사] 특가법위반(도주차량)으로 기소됐으나, 국민참여재판을 통해 무죄가 선고된 사건
19725 [민사] 상속인들이 근로자인 피상속인의 부양가족이었다면, 피상속인의 퇴직금 절반 및 퇴직연금을 수령하였더라도, 상속의 단순승인 사유인 ‘상속인이 상속재산에 대한 처분행위를 한때’에 해당하지 않는다고 본 사건(울산지방법원 2017가단16791)
20597 [상표]확인대상표장은 상표로서 사용된 것으로 볼 수 없다고 한 사례(특허법원 2018허6603)
18854 [행정] 모친 간병이라는 특수한 사정으로 의무복무기간을 채우지 못하였더라도 위탁교육훈련비를 반환해야 한다고 본 사안(창원지방법원 2016구합52819)
19287 [민사] 보행자신호에 자전거를 타고 횡단보도를 건너다가 횡단보도를 벗어난 지점에서 우회전 차량과 충돌한 경우 자전거 탑승자에게도 20%의 과실이 있다고 판시한 사례 [2016가단5123450]
20161 [민사] 휴대전화 카메라로 직원의 신체를 몰래 촬영한 회사 대표에게 위자료 지급을 명한 사건(울산지방법

...

3121 [형사] 자살방조--피고인이 피해자에게 “그럼, 그냥 죽어라. 죽을 테면 죽어봐”라고 말하면서 라이터를 건네 줄 당시 피해자가 이를 이용하여 분신하여 자살할 수도 있다는 점을 인식하면서 위와 같은 행위를 한 경우의 판결
2680 법률상 배우자 사이의 혼인관계가 사실상 해소된 상태에 있지 않고, 사실혼 관계가 중혼적 사실혼 관계에 지나지 않는 경우, 사실혼 관계에 있는 배우자를 산업재해보상보험법상 유족으로 볼 수 없다고 판시한 사례(2007. 11. 1. 선고 2007구합21051 판결)
928 [형사]동급생을 살인한 혐의로 기소됐던 고교생에 대하여 제1심에서 무죄를 선고한 사례
3992 새마을금고의 대의원선거상 하자가 중대하여 무효라고 본 사례
4422 [민사] 화물차 위수탁계약의 해지와 관련된 법률관계
1366 청소년보호법위반죄의 성립 여부에 관한 사례
52 서울중앙지방법원 2005. 11. 4. 선고 2004고합1389  등 판결
490 산업자원부장관의 원자력발전시설 건설사업을 위한 전원개발사업 실시계획승인에 있어 절차적 요건 준수여부와 재량의 일탈.남용여부를 판단한 사례
1805 미성년 동료딸 상습 성추행 ‘중형’
4860 연장근로는 당사자 간의 합의에 의하여야 하고, 이는 원칙적으로 사용자와 개별 근로자 사이의 개별적 합의를 의미하나, 이와 같은 합의는 근로계약 등으로 미리 약정할 수 있음은 물론, 개별근로자의 연장근로에 관한 합의권을 박탈하거나 제한하지 아니하는 범위에서는 단체협약에 의한 합의도 가능하다 할 것이나, 한편, 연장근로는 근로자의 건강에 위협이 되고 생활의 불안정을 증가시키는 것이므로 이를 엄격히 해석할 필요가 있고, 연장근로가 원래 업무상 예측하기 어려운 수요 등에 대응하기 위하여 예외적으로 인정된 것임을 고려하면, 근로자의 합의권을 실질적으로 보장하기 위해서는 연장근로에 대한 근로자의 예견가능성이 보장되어야 한다는 판결
3551 폭행등을 이유로 한 파양
3120 "학교환경위생정화구역(상대정화구역) 내에서 게임장을 할 수 있도록

3541 공사현장 돌아다니며 돈 뜯어낸 기자들에 대하여 중형을 선고한 사례
3111 해고무효확인 판결
917 공직선거법위반(후보자 명예훼손)
2230 분양계약을 가장한 수분양자들은 주택분양보증제도의 취지상 그 보호대상이 될 수 없다.
3981 조성물 발명에 있어 그 구성으로 포함되어야 할 적극적 구성요건과 함께 어떤 요소가 배제되어야 할 것을 내용으로 하는 소극적 구성요건이 기재된 경우, 소극적 구성요건 그 자체로는 독립된 기능을 발휘할 수 없을 것이므로, 그러한 경우 소극적 구성요건에서 배제하고 있는 어떠한 요소가 없는 상황하에서만 나머지 구성이 작동한다거나 현저히 효과가 증대된다는 특별한 사정이 있는 경우에만 소극적 구성요건이 기술적으로 의미 있는 발명의 구성요건으로 된다고 할 것이다.
1790 번호계가 파계된 경우 계불입금의 정산방법
4411 석축 중 일부가 붕괴되어 토사가 유출되어 개발행위허가를 취소한 사안에서 위 결과는 기록적인 집중호우를 기록한 태풍 나리로 인한 것이어서 개발행위허가취소처분을 취소한 사례
1355 대덕연구개발특구의 녹지지역 개발행위를 제한한 유성구청 처분의 정당성을 수긍한 판결
34 특허법원 2005. 12. 22. 선고 2005허278 판결 [권리범위확인(상)]
2669 이중주차된 차량을 밀다가 사고가 발생한 경우 책임 여부
479 독일 종묘회사가 장미 종자에 대하여 로얄티 지급을 청구한 사례(2006.3.31.선고)
3540 점유취득시효완성을 위한 자주점유에의 해당 여부
4849 매매계약을 체결하면서 죽은 사람을 상대로 소를 제기하여 의제자백판결을 받아 이전등기를 경료하기로 약정한 경우에 매매계약이 사회질서에 위반되어 무효라고 하면서, 매도인의 불법성이 현저하므로 수령한 계약금을 반환하여야 한다고 한 사례
3110 형사재심청구인 사망시 소송종료선언을 해야한다는 결정문
916 공직선거법위반(기부행위) 사건
1789 뇌수막염 감기로 오진 사망 배상(2007. 3. 15. 선고)
3980 비교대상발명에 출원발명의 구성요소 중 하나인 “

4835 [행정] 어장이용개발계획 수립여부는 행정소송의 대상이 아니라고 각하한 사례
3531 근로기준법상의 근로자에 해당하는지 여부
2219 지점에서 인적 물적 설비를 갖추어 계속하여 사무 또는 사업을 행하지 아니한 경우 등록세 중과세 요건인 대도시 내에서의 지점 설치에 따른 부동산등기’에 해당하지 아니한다고 본 사례(2007. 7. 10. 선고 2007구합1491 판결)
1345 집회참가자들에 의한 차량 파손에 대하여 집회주최자가 불법행위책임을 지는지 여부
1780 관할관청의 건축불허가처분이 위법하다고 한 사례
24 특허법원 2005. 12. 16. 선고 2005허1059 판결 [등록무효(특)]
3971 부산교통공사로부터 지하상가의 분양사업권자로 선정되지 않은 피고인이 관련 법령상 금지된 사전 분양을 하였는지에 대하여 판단한 사례(무죄)
469 정신과전문의가 입원 진단하여 입원을 시킨행위가 감금죄에 해당하는지 여부
2659 ○ 출판물에 의한 명예훼손죄에 있어서 공공의 이익을 위하여 진실하거나 진실하다고 믿을 만한 상당한 이유가 있는 사실을 적시한 경우 위법성이 조각되는지 여부 등
3099 백혈병 소아에 대한 시술 의사의 업무상과실치사죄 성립 여부
4401 부동산이 토지수용대상으로 택지개발사업으로 인한 용도지역의 변경과 개발제한구역의 해제가 예정되어 막대한 개발이익을 기대할 수 있다고 하여도 소유자가 이를 매도하지 않고 소유하는 것이 불가능하였는데 B가 향유할 수 없었던 개발이익이 포함된 상속개시시의 시가를 기준으로 기초재산의 가액을 산정하는 것은 불합리하며, 유류분이 상속개시 당시의 피상속인의 재산 중 상속인에게 유보되는 일정 비율의 몫이라는 점에서 위와 같이 상속개시 당시 피상속인의 재산이 될 수 없었던 부분을 유류분의 전제로 삼는 것은 부적절해 보이는 점 등을 고려하면, 이 사건의 경우 기초재산의 가액은 B가 위 부동산들을 매도하면서 실제 수령한 돈에 물가상승률을 반영한 금액으로 산정함이 상당하다는 판결
906 두산그룹 총수일가 항소심판결(2006.7.2

1335 [형사] 인터넷 도박 사이트 운영 사건(원주지원 2006고단871)
2208 유흥주점의 유흥접객원으로 고용되면서 받은 선불금에 관한 반환약정의 유효 여부
14 특허법원 2005. 11. 10. 선고 2005허5112 판결 [등록무효(상)]
1769 6.25때 총상.. 인우보증을 믿고 유공자 인정(2007. 3. 30. 선고)
3088 법인세법 제76조 제5항의 가산세는 실제의 거래가 있음에도 그 지출증빙서류를 수취하지 않은 경우에 적용되고, 실제의 거래가 없음에도 거래가 있는 것으로 위장하여 증빙서류를 수수한 행위에 대하여는 적용되지 아니한다고 본 판결
4390 학내분규 과정에서 원고 학생, 학부모들이 피고 교수들과 학교법인의 기말고사 성적입력 지연, 강의거부 등으로 인하여 정신적 손해를 입었다면서 제기한 위자료청구를 배척한 사례(2008.9.26.선고)
3520 헬멧미착용을 이유로 무리한 교통단속을 벌이다 법규위반자가 사망한 사례에서 국가의 책임 및 책임비율
893 개정된 시의회 조례안이 시행되기 전에 새로 편입될 예정구역에 미리 의정보고서를 배포한 전 구의회의원에게 엄정한 형사책임을 물은 사례
4823 공정증서에 의한 유언의 요건을 갖추지 못한 경우 증서진부확인의 소는 소의 이익이 없다고 본 판결
2648 [민사] 양도약정을 이유로 상속인들에게 소유권이전등기절차 이행 청구한 사건(속초지원 2007가단1267)
1334 대한민국이 T-50 주익 생산 주체 변경에 따른 권리포기대가금(물량보상비)을 부담하는 것이 공무원의 착오에 의한 국고손실에 해당하는지 여부
458 마약범죄에 있어서의 함정수사
2207 친일 전력이 있는 조상의 땅을 매도하겠다며 사기 범행을 한 피고인에게 실형을 선고한 사례
3960 의용소방대 유급상비대원으로 화재진압작업 중 사망한 자의 국가유공자 등록신청의 적법성
13 특허법원 2005. 11. 3. 선고 2004허6521 판결 [등록무효(특)]
1768 원청회사를 하청업체 근로자의 노조법상 사용자로 인정한 판결(2007. 4. 11

883 상표법 제7조 제1항 제12호의 동일 또는 유사한 상표
448 상표법 제73조 제1항 제2호의 판단기준
2638 [행정] 교사 임용시험 불합격처분취소 청구 사건(춘천지방법원 2005구합706, 713)
3 특허법원 2005. 10. 13. 선고 2005허2328 판결 [등록무효(특)]
3950 허가 없이 외화를 수출하려 하였다는 이유로 외국환거래법위반으로 기소된 사안에서, 피고인이 국제공항 내 면세점에 물품대금을 지급하기 위하여 외화를 휴대하였다는 이유로 무죄를 선고한 사례
1757 배임죄의 성립여부에 관한 사례
3077 가장 임차인에게 실형을 선고한 사례
1323 부친을 구타하여 사망에 이르게 한 존속상해치사죄에 대하여 집행유예를 선고한 사례
3509 소득세법 제94조 제1항 제3호가 양도소득세 과세대상으로 규정한 ‘신주인수권’에는 ‘주주의 신주인수권’ 뿐만 아니라 ‘신주인수권부사채의 신주인수권’도 포함된다는 이유로, 신주인수권부사채에 딸린 신주인수권의 양도차익에 대하여 양도소득세를 과세한 것이 적법하다고 본 판결
2196 자살한 학생의 유가족이 학교내 괴롭힘을 저지른 학생과 그 부모를 상대로 제기한 손해배상청구소송에서 원고 일부승소 판결한 사례 -이른바 ‘학교내 왕따’사건에서 위자료의 지급을 인정한 사례-
882 보정 전 출원발명을 심판대상으로 한 심결의 위법 여부
447 의약품인 지정상품에 외국어상표 “ELOCOM”과 그 한글음역상표 “에로콤”이 함께 표기되는 사정이 인정되는 경우 그 외국어상표의 호칭은 “엘로콤”이 아니라 “에로콤”으로 보아야 한다고 판단한 사례
3949 일조권 및 사생활침해를 이유로 손해배상책임을 인정한 사례
2637 [민사] 타인의 토지를 도로로 점유 및 사용함을 이유로 부당이득반환 청구한 사건(원주지원 2005가단8759)
2 특허법원 2005. 10. 13. 선고 2005허5631 판결 [등록무효(상)]
1756 도급제 신문배달사원에 대하여 그 근무형태, 보수 지급방식, 업무의 대체성 등에 비추어 근로자에 해당하지 않는다고

In [8]:
df = pd.DataFrame(data=ret)
df.to_excel('all_judge.xlsx')

In [9]:
df

content        date seqnum  \
0      \n  \r\n1. 사안의 개요\n  \n- 원고는 의료기관을 개설하여 운영하고 있...  2019-10-01  21063   
1      \n \n1. 사안의 개요\n \n  - 원고는 장교로 OO학교에서 근무하다가 상관...  2019-10-01  21062   
2      \n \n[형사] 서울남부지방법원 2019. 9. 23. 선고 2019고합127\n...  2019-09-30  21061   
3      \n\n▶ 피고는 병에게 배우자가 있음을 알면서도 병과 부정행위를 함으로써 원고의 ...  2019-09-23  21060   
4      \n\n▶ 원고는, 피고가 병이 배우자 있는 자 임을 알면서도 중혼적 사실혼 관계를...  2019-09-23  21059   
5      \n\n▶ 피고 을은 실제로는 피고 병이 원고의 친생자가 아님에도 불구하고 원고에게...  2019-09-23  21058   
6      \n\n▶ 피고 을은 원고를 속이고 오랜 기간 피고 병과 부적절한 만남을 유지하는 ...  2019-09-23  21057   
7      \n\n▶ 원고는, 피고가 과거에 두 차례 혼인하였다가 이혼한 적이 있고, 초혼 배...  2019-09-23  21056   
8      \n\n▶ 가부장적이고 강압적인 성격의 피고는 혼인기간 동안 자신이 세운 기준과 잣...  2019-09-23  21055   
9      \n[형사-국민참여재판] 폭행치사\n \n피고인이 피해자의 얼굴을 1회 강하게 가격...  2019-09-19  21054   
10     \n[형사] 특정범죄가중처벌등에관한법률위반(도주치상), 도로교통법위반(음주운전)\n...  2019-09-19  21053   
11     \n \n1. 대전지방법원 2019. 8. 23. 선고 2019고단214 판결\n ...  2019-09-19  21051   
12     \n인천지방법원 2019. 9. 18. 선고 2017가단232913 판결\n \n▣...  2019-09-18  21050   
13     \n상가를 신축한 피고E와 위 상가 중 ‘I호’ 점포에 관하여 분양계약을 체결한 원...  2019-09-18  21049   
14     \n\n\n\n\n\n\n\n\n\n\n★창원지방법원 2019. 7. 17. 선고 ...  2019-09-17  21048   
15     \n\n\n\n\n\n★창원지방법원 2019. 7. 18. 선고 2019고합89 판...  2019-09-17  21047   
16     \n\n\n\n\n\n★창원지방법원 2019. 7. 17. 선고 2018고단2479...  2019-09-17  21046   
17     \n\n\n\n\n\n★창원지방법원 2019. 7. 19. 선고 2019고단1321...  2019-09-17  21045   
18     \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n★창원지방법원 2019. ...  2019-09-17  21044   
19     \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n★창원지방법원 2019. ...  2019-09-17  21043   
20     \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n★창원지...  2019-09-17  21042   
21     \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n★창원지방법원 2019. ...  2019-09-17  21041   
22     \n\n\n\n\n\n\n\n\n\n\n★창원지방법원 2019. 2. 20. 선고 ...  2019-09-17  21040   
23     \n\n\n\n\n\n\n\n\n\n\n★창원지방법원 2019. 7. 4. 선고 2...  2019-09-17  21039   
24     \n\n\n\n\n\n\n\n\n\n\n★창원지방법원 2019. 7. 11. 선고 ...  2019-09-17  21038   
25     \n\n\n\n\n\n\n\n\n\n\n★창원지방법원 2019. 7. 4. 선고 2...  2019-09-17  21037   
26     \n\n\n\n\n\n★창원지방법원 2019. 6. 27. 선고 2018가합5272...  2019-09-17  21036   
27     \nl  사건 개요 및 판시 요지\n다음과 같은 사정들을 고려하여 보면, 구 상표법...  2019-09-16  21035   
28     \nl  사건 개요 및 판시 요지\n다음과 같은 사정들을 고려하여 보면, 2013....  2019-09-16  21034   
29     \nl  사건 개요 및 판시 요지\n확인대상발명의 (ii) 과립은 이 사건 제41항...  2019-09-16  21033   
...                                                  ...         ...    ...   
20738  \n사건 : 특허법원 2005. 12. 23. 선고 2005허6542 판결 [등록취...  2005-12-23     30   
20739  \n사건 : 특허법원 2005. 12. 23. 선고 2005허1455 판결 [등록무...  2005-12-23     29   
20740  \n사건 : 특허법원 2005. 12. 22. 선고 2005허6061 판결 [권리범...  2005-12-23     28   
20741  \n사건 : 특허법원 2005. 12. 15. 선고 2004허8602 판결 [등록무...  2005-12-23     27   
20742  \n사건 : 특허법원 2005. 12. 16. 선고 2005허1660 판결 [등록무...  2005-12-19     26   
20743  \n사건 : 특허법원 2005. 12. 16. 선고 2005허1653 판결 [등록무...  2005-12-19     25   
20744  \n사건 : 특허법원 2005. 12. 16. 선고 2005허1059 판결 [등록무...  2005-12-19     24   
20745  \n사건 : 특허법원 2005. 12. 8. 선고 2005허384 판결 [등록무효(...  2005-12-19     23   
20746  \n사건 : 특허법원 2005. 12. 8. 선고 2005허2564 판결 [거절결정...  2005-12-15     22   
20747  \n사건 : 특허법원 2005. 12. 2. 선고 2005허1042 판결 [권리범위...  2005-12-02     21   
20748  \n사건 : 특허법원 2005. 12. 1. 선고 2005허3673 판결[거절결정(...  2005-12-02     20   
20749  \n사건 : 특허법원 2005. 12. 1. 선고 2005허3666 판결[거절결정(...  2005-12-02     19   
20750  \n사건 : 특허법원 2005. 11. 24. 선고 2004허5603 판결 [등록무...  2005-11-29     18   
20751  \n사건번호 : 특허법원 2005. 11. 25. 선고 2005허7088 판결 [거...  2005-11-25     17   
20752  \n사건번호 : 특허법원 2005. 11. 25. 선고 2005허537 판결 [거절...  2005-11-25     16   
20753  \n사건번호 : 특허법원 2005. 11. 24. 선고 2005허7682 판결 [권...  2005-11-24     15   
20754  \n사건번호 : 특허법원 2005. 11. 10. 선고 2005허5112 판결 [등...  2005-11-21     14   
20755  \n사건 : 특허법원 2005. 11. 3. 선고 2004허6521 판결 [등록무효...  2005-11-10     13   
20756  \n사건 : 특허법원 2005. 10. 27. 선고 2005허3413 판결 [권리범...  2005-11-04     12   
20757  \n사건 : 특허법원 2

In [ ]:
all_judge_list_re = []

for i in crawl_view_param_list[5000:7000]:
    judge_dic = crawl_judge(i)
    all_judge_list.append(judge_dic)
    print(i, judge_dic['title'])
    
df = pd.DataFrame(data=all_judge_list)
df.to_excel('all_judge.xlsx')

In [175]:
test=['[민사]', '[형사-국민참여재판]', '[등록무효(의)]', '[6. 24.자 신청]', 'There is no pattern']
pattern = re.compile('(?<=\[).+?(?=\])')
for i in test:
    print(extract_tag(i))

민사
형사-국민참여재판
등록무효(의)
6. 24.자 신청
None


In [138]:
judge_dic = crawl_and_save_pdf(crawl_view_param_list[2])

In [72]:
#crawl_view_param_list[4500]
crawl_judge(crawl_view_param_list[10000])
#save_judge()

10987 [민사] 학교급식종사원의 정리해고를 무효로 본 사례


{'title': '[민사] 학교급식종사원의 정리해고를 무효로 본 사례',
 'writer': '울산지방법원',
 'date': '2013-06-05',
 'content': '\n',
 'seqnum': '10987',
 'tag': '민사'}

In [52]:
#all_judge_list = []

for i in crawl_view_param_list[5000:7000]:
    judge_dic = crawl_judge(i)
    all_judge_list.append(judge_dic)
    print(i, judge_dic['title'])
    
df = pd.DataFrame(data=all_judge_list)
df.to_excel('all_judge.xlsx')

{'seqnum': '16019', 'cbub_code': '000411'} [형사]2015고합234 공용선박방화미수, 폭력행위등처벌에관한법률위반(집단·흉기등재물손괴등), 선박침입
{'seqnum': '16018', 'cbub_code': '000411'} [형사]2015고합191 상습강제추행
{'seqnum': '16017', 'cbub_code': '000411'} [형사]2015고합212 살인
{'seqnum': '16016', 'cbub_code': '000411'} [형사]2015고합162 성폭력범죄의처벌등에관한특례법위반(장애인준강간)
{'seqnum': '16015', 'cbub_code': '000411'} [형사]2015고합153 현주건조물방화, 폭행
{'seqnum': '16014', 'cbub_code': '000411'} [형사]2015고단1884 사기
{'seqnum': '16013', 'cbub_code': '000411'} [형사]2014고정2208 청소년보호법위반
{'seqnum': '16012', 'cbub_code': '000530'} [행정] 2015. 10. 21.자 주요간선도로변에 무인텔 건축허가 신청을 불허한 것이 정당하다는 판단
{'seqnum': '16011', 'cbub_code': '000213'} [민사] 임차인이 주택재개발정비사업조합에게 보증금반환을 청구할 수 있다고 본 사례(확정)
{'seqnum': '16010', 'cbub_code': '000213'} [민사] 경매절차에서 구분건물을 매수한 매수인이 대지지분을 취득한다고 판단한 사례(확정)
{'seqnum': '16009', 'cbub_code': '000280'} [2015. 9. 18. 형사] 노숙자들을 감금하여 처벌된 사례
{'seqnum': '16008', 'cbub_code': '000280'} [2015. 9. 24. 형사] 인터넷 신문 보도를 통한 허위사실공표를 이유로 공직선거법위반죄 등으로 처벌된 사례
{'seqnum': '16007', 'c

{'seqnum': '15933', 'cbub_code': '000230'} 유책배우자의 이혼청구를 배척한 판결
{'seqnum': '15932', 'cbub_code': '000700'} [2015. 9. 10.자 상표]식당에서 메뉴에 제공된 것이 서비스표적 사용은 될 수 있더라도, 상표적 사용은 아니라고 본 사례
{'seqnum': '15931', 'cbub_code': '000411'} [형사]2015고단1393 성폭력범죄의처벌등에관한특례법위반(카메라등이용촬영), 협박
{'seqnum': '15930', 'cbub_code': '000411'} [형사]2015고단1741 근로기준법위반, 부동산실권리자명의등기에관한법률위반
{'seqnum': '15929', 'cbub_code': '000318'} 8개월가량 혼인관계를 유지해 오던 원고(아내)와 피고(남편)가 서로의 귀책을 이유로 상호 간에 이혼 및 위자료, 재산상 손해배상 등을 구한 사안에서, ① 피고가 혼인기간 동안 유흥업소에 출입하며 수시로 다수의 여성들과 연인관계에서나 있을 법한 부적절한 내용의 문자메시지를 주고받는 등의 행위를 한 것이 부정행위에 해당한다고 판단하여 원고의 본소 이혼 및 위자료 청구를 일부 인용하고, ② 나아가 원고와 피고가 8개월가량 혼인관계를 유지하여 온 이상 혼인이 단기간에 파탄되었다거나 피고가 당초부터 혼인을 유지할 의사가 없었다는 등의 특별한 사정을 인정하기 어렵다는 이유로, 혼인을 위하여 지출한 예식비, 예단비 등 각종 비용 상당액의 손해배상을 구할 수는 없다고 판단하여 원고의 본소 재산상 손해배상 청구를 기각한 사례
{'seqnum': '15928', 'cbub_code': '000411'} [형사]2015고단1335 근로기준법위반, 근로자퇴직급여보장법위반
{'seqnum': '15927', 'cbub_code': '000411'} [형사]2015고단115, 2015고단494(병합), 2015고단1747(병합) 근로기준법위반, 근로자퇴직급여보장법위반
{'seqnum': 

{'seqnum': '15860', 'cbub_code': '000214'} [형사] 승용차의 앞, 뒤를 트랙터와 1톤 화물차량으로 약 1시간 30분 동안 가로막아 승용차 소유자로 하여금 차량을 운행하지 못하도록 한 사안에 대하여, 피고인의 그러한 행위만으로는 승용차가 가지는 본래의 효용을 침해한 정도에는 이르지 못하므로 형법 제366조의 재물손괴죄에는 해당하지 않는다고 판단한 사례
{'seqnum': '15859', 'cbub_code': '000214'} [형사] 피해자가 자전거를 타고 중랑천 자전거도로를 가던 중 목줄을 하지 않은 채 갑자기 나타난 애완견을 피하려다 넘어져 중상을 입은 사건에서, 애완견 소유자에게 애완견의 관리를 소홀히 한 점을 들어 과실치상죄로 벌금을 선고한 사례
{'seqnum': '15858', 'cbub_code': '000520'} [전주지방법원 민사] 2015. 9. 21. 선고 2014나9970 추심금
{'seqnum': '15857', 'cbub_code': '000520'} [전주지방법원 민사] 2015. 9. 21. 선고 2014나9918 구상금
{'seqnum': '15856', 'cbub_code': '000200'} [2015. 9. 22.자 행정] 가.PNA 칩이 부착된 탐침을 사용한 인유두종바이러스 진단방법이 기존의 보험급여대상(인유두종바이러스 유전자형 검사)에 포함되는지 여부(적극) 나. 신의료기술결정의 의미 및 효력 다. 국민건강보험법 제57조 제1항 또는 의료급여법 제23조 제1항의 ‘속임수 기타 부당한 행위로 급여비용을 받은 경우의 의미
{'seqnum': '15855', 'cbub_code': '000211'} [형사] 유기치사죄에 대한 판결
{'seqnum': '15854', 'cbub_code': '000211'} [형사] 존속살해 등에 대한 판결
{'seqnum': '15853', 'cbub_code': '000410'} [형사]  피해자가 돈을 빌리고 갚지 않는다는 이유로 성매매를 강요하는 등의 

{'seqnum': '15779', 'cbub_code': '000410'} [행정]  벌금 수배사실에 관한 개인정보를 사적으로 조회하고 알려준 경찰관에 대한 징계처분이 적법하다고 인정한 판결
{'seqnum': '15778', 'cbub_code': '000410'} [형사]  음주상태에서 승용차를 운전하여 파출소로 돌진하고 차량에 불을 붙인 피고인에게 징역 1년 6월을 선고한 판결
{'seqnum': '15777', 'cbub_code': '000410'} [형사]  업무상 과실로 피해자에게 상해를 입힌 의사에게 금고 6월을 선고한 판결
{'seqnum': '15776', 'cbub_code': '000410'} [형사]  걸어가지 않고 순찰차를 타고 가자고 한다는 이유로 경찰관을 폭행한 피고인에게 징역 8월을 선고한 판결
{'seqnum': '15775', 'cbub_code': '000410'} [민사] 백화점에서 절취한 자동차를 운전하다 낸 교통사고에 대하여 백화점의 손해배상책임이 없다고 인정한 판결
{'seqnum': '15774', 'cbub_code': '000411'} [형사]2015고단1129 사기
{'seqnum': '15773', 'cbub_code': '000411'} [형사]2015고단1000 공문서변조, 변조공문서행사
{'seqnum': '15772', 'cbub_code': '000411'} [형사]2015고단956, 1520(병합), 1720(병합) 사기, 상습절도, 여신전문금융업법위반, 사기미수
{'seqnum': '15771', 'cbub_code': '000411'} [형사]2015고단906 공기호위조, 위조공기호행사
{'seqnum': '15770', 'cbub_code': '000411'} [형사]2015고단412, 2015고단1653(병합) 사기, 여신전문금융업법위반, 사문서변조, 변조사문서행사
{'seqnum': '15769', 'cbub_code': '000411'} [형사]2015고단39 사기
{'seqnum': 

{'seqnum': '15705', 'cbub_code': '000214'} [행정] 개인택시 운송사업면허를 발급받고자 하는 사람이 하여야 하는 운전경력의 증명은, 여객자동차 운수사업법 시행규칙 제19조 및 이에 근거하여 지방자치단체가 제정한 '개인택시 운송사업면허 업무처리규정'에서 정하는 서류와 동등한 정도의 객관적이고 합리적인 증거자료에 의하여야 한다고 판단한 사례
{'seqnum': '15704', 'cbub_code': '000214'} [상사] 권리금 6,000만원을 받고 음식점 영업을 양도한 사람이 그 음식점 인근에 새로운 음식점을 개업한 사안에 대해, 영업양도인은 양도일로부터 10년간 의정부시 지역에서 동종 음식점 영업을 하여서는 아니 된다고 판단한 사례
{'seqnum': '15703', 'cbub_code': '000214'} [형사] 호랑이 나무조각상(높이 40cm, 너비 30cm)을 바닥에 던지는 방법으로 피해자를 협박한 사건에서, 호랑이 나무조각상은「폭력행위 등 처벌에 관한 법률」제3조 제1항 소정의 ‘위험한 물건’에 해당한다고 판단한 사례
{'seqnum': '15702', 'cbub_code': '000214'} [형사] 어린이집 원장인 피고인이 스펀지 블록으로 피해아동(생후 28개월)의 머리를 때린 행위에 대해, 피고인은 훈육 차원일 뿐 아동을 학대할 의도가 아니었다고 주장하며 항소하였으나, 정서적 학대행위에 해당한다는 이유로 피고인의 항소를 기각한 사례
{'seqnum': '15701', 'cbub_code': '000411'} [민사]2013나6636 채무부존재확인
{'seqnum': '15700', 'cbub_code': '000411'} [민사]2014나7827 부당이득금
{'seqnum': '15699', 'cbub_code': '000411'} [민사]2014나8172 소유권이전등기
{'seqnum': '15698', 'cbub_code': '000420'} [형사]허위 세금계산서 발행에 벌금 14억 선고한 사례
{'seq

...

{'seqnum': '14988', 'cbub_code': '000240'} [형사] 검찰청 통역인으로서 피의자들로부터 통역경비와 청탁 명목으로 금원을 편취한 피고인에 대하여 징역 8월에 집행유예 2년을 선고한 사건
{'seqnum': '14987', 'cbub_code': '000240'} [형사] 사전에 승용차 브레이크를 고장나게 하여 피해자를 살해하려고 하였으나 미수에 그친 자동차정비사인 피고인에 대하여 징역 2년에 집행유예 3년을 선고한 사건
{'seqnum': '14986', 'cbub_code': '000411'} [형사]2014고합377 강제추행치상, 강제추행
{'seqnum': '14985', 'cbub_code': '000411'} [형사]2014고합340 특정경제범죄가중처벌등에관한법률위반(사기), 사기
{'seqnum': '14984', 'cbub_code': '000411'} [형사]2014고합311 존속살해미수, 현주건조물방화미수
{'seqnum': '14983', 'cbub_code': '000411'} [행정]2014구합1998 자동차운전면허취소처분취소
{'seqnum': '14982', 'cbub_code': '000215'} [민사] 위약벌 부과 약정 무효 여부
{'seqnum': '14981', 'cbub_code': '000310'} [민사] 대구지방법원 2015. 5. 15. 선고 2014가단122273 가등기말소 판결
{'seqnum': '14980', 'cbub_code': '000318'} 원고가 1년 이상 사실혼관계를 유지해 온 피고를 상대로 사실혼관계의 부당 파기에 따른 위자료 및 사실혼기간 동안 피고에게 생활비 등 각종 명목으로 교부한 돈과 피고로 인하여 지출한 각종 비용(혼수비용, 주말부부 내지 별거생활을 하면서 지출한 월세)에 대한 재산상 손해배상 내지 원상회복을 구한 사안에서, ① 사실혼 파탄의 책임이 쌍방 모두에게 있고 그 책임의 정도가 동등한 이상 위자료 청구는 받아들일 수 없고, ② 나아가 원고와 피고가 

{'seqnum': '14915', 'cbub_code': '000280'} [2015. 5. 1. 형사] 의료기관의 개설자가 될 수 없는 자가 의료기관을 개설하여 처벌된 사례
{'seqnum': '14914', 'cbub_code': '000280'} [2015. 5. 7. 형사] 도로교통법상 사고 후 미조치의 죄책을 인정한 사례
{'seqnum': '14913', 'cbub_code': '000530'} [고등민사] 2015. 5. 13.자 청소차량을 운전하는 환경미화원도 쓰레기 수거를 하는 사람과 동일한 임금을 지급하여야 한다고 선고한 사안
{'seqnum': '14912', 'cbub_code': '000240'} [행정] 제출된 해산동의서 중 일부가 무효여서 과반수의 해산동의가 없다는 이유로 조합설립인가취소처분이 위법하다고 본 사례
{'seqnum': '14911', 'cbub_code': '000240'} [행정] 친구들의 성기와 엉덩이를 만졌다는 이유로 초등학생에게 내려진 전학처분이 재량을 벗어나 위법하다고 본 사례
{'seqnum': '14910', 'cbub_code': '000240'} [형사] 회사동료와의 음주 모임에서 피해자를 유사강간한 피고인에게 국민참여재판을 거쳐 징역 2년을 선고한 사건


ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.



Traceback (most recent call last):
  File "/home/hangyeol.sun/anaconda3/lib/python3.6/site-packages/IPython/core/interactiveshell.py", line 3325, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "<ipython-input-52-d1ef7bf9bde3>", line 4, in <module>
    judge_dic = crawl_judge(i)
  File "<ipython-input-50-7e65ac6d2fa1>", line 20, in crawl_judge
    r = requests.post("https://www.scourt.go.kr/portal/dcboard/DcNewsViewAction.work?gubun=44", data = view_param)
  File "/home/hangyeol.sun/anaconda3/lib/python3.6/site-packages/requests/api.py", line 116, in post
    return request('post', url, data=data, json=json, **kwargs)
  File "/home/hangyeol.sun/anaconda3/lib/python3.6/site-packages/requests/api.py", line 60, in request
    return session.request(method=method, url=url, **kwargs)
  File "/home/hangyeol.sun/anaconda3/lib/python3.6/site-packages/requests/sessions.py", line 533, in request
    resp = self.send(prep, **send_kwargs)
  File "/home/hangyeol.sun/anacond

KeyboardInterrupt: 

In [53]:
len(all_judge_list)

2784

In [180]:
df = pd.DataFrame(data=all_judge_list)
df.to_excel('all_judge.xlsx')

In [82]:
with open('crawl_vp.txt', 'w') as filehandle:
    for listitem in crawl_view_param_list:
        filehandle.write('%s\n' % listitem)

In [9]:
action = "/portal/dcboard/DcNewsListAction.work?gubun=44"

In [37]:
#parameters = {'pageIndex':'10'}
#r = requests.post("https://www.scourt.go.kr/portal/dcboard/DcNewsListAction.work?gubun=44", data = parameters)
parameters = crawl_view_param_list[4075]
r = requests.post("https://www.scourt.go.kr/portal/dcboard/DcNewsViewAction.work?gubun=44", data = parameters)

In [40]:
soup = BeautifulSoup(r.text, 'html.parser')
soup.find_all('th', text=re.compile('작성일'))[0].find_next_siblings('td')[0].text
#writer = soup.find_all(text=re.compile('작성자'))[0].parent.find_next_siblings('td')[0].text

'2016-03-30'

In [22]:
print(r.text)



<!DOCTYPE html PUBLIC "-//W3C//DTD HTML 4.01 Transitional//EN" "http://www.w3.org/TR/html4/loose.dtd">


<html lang="ko">
 <head>
 	










<meta http-equiv="X-UA-Compatible" content="IE=edge,chrome=1">
<meta name="viewport" content="width=device-width, initial-scale=1.0, maximum-scale=3.0, minimum-scale=1.0, user-scalable=yes, target-densitydpi=medium-dpi">
<link rel="shortcut icon" href="/scourt/common/images/favicon.ico" type="image/x-icon" />
<script type="text/javascript" src="/js/portal/jquery-1.8.3.js"></script>
<script type="text/javascript" src="/js/portal/jquery-ui-1.8.21.custom.min.js"></script>
<script type="text/javascript" src="/js/portal/common_old.js" charset="euc-kr"></script>
<script type="text/javascript" src="/js/portal/common.js"></script>
<script type="text/javascript" src="/js/portal/embed.js"></script>

<!-- <link rel="stylesheet" type="text/css" href="/css/jquery.ui.datepicker.css">  -->
<!-- <link rel="stylesheet" type="text/css" href="/css/jquery-ui-1.8.

In [41]:
pdf_url = "http://file.scourt.go.kr//AttachDownload?file=1567473540799_101900.pdf&path=003&downFile=2018%C7%E38210.pdf"
urlretrieve(pdf_url, "pdf/test.pdf")

('pdf/test.pdf', <http.client.HTTPMessage at 0x7fd6b04a4cf8>)

In [34]:
pdf_url[73:75]

'th'

In [44]:
def convert_pdf_to_txt(path):
    rsrcmgr = PDFResourceManager()
    retstr = StringIO()
    codec = 'utf-8'
    laparams = LAParams()
    device = TextConverter(rsrcmgr, retstr, codec=codec, laparams=laparams)
    fp = open(path, 'rb')
    interpreter = PDFPageInterpreter(rsrcmgr, device)
    password = ""
    maxpages = 0
    caching = True
    pagenos=set()

    for page in PDFPage.get_pages(fp, pagenos, maxpages=maxpages, password=password,caching=caching, check_extractable=True):
        interpreter.process_page(page)

    text = retstr.getvalue()

    fp.close()
    device.close()
    retstr.close()
    return text

In [46]:
convert_pdf_to_txt("pdf/test.pdf")

"특\n\n허\n\n법\n\n원\n\n제\n\n1 부\n\n판\n\n결\n\n사       건\n\n2018허8210  거절결정(특)\n\n원       고\n\n주식회사 A\n\n대표이사 B\n\n소송대리인 특허법인 공간\n\n담당변리사 백경업, 김은희\n\n피       고\n\n특허청장\n\n소송수행자 박정민\n\n변 론 종 결\n\n2019. 4. 18.\n\n판 결 선 고\n\n2019. 5. 30.\n\n1. 원고의 청구를 기각한다. \n\n2. 소송비용은 원고가 부담한다. \n\n주\n\n문\n\n청 구 취 지\n\n- 1 -\n\n\x0c특허심판원이 2018. 8. 31. 2018원2091호 사건에 관하여 한 심결을 취소한다.\n\n이\n\n유\n\n1.  기초사실\n\n 가. 이 사건 출원발명(갑 제3, 7, 10, 12호증)1)\n\n  1)  발명의  명칭:  육산화사비소를 포함하는 암 전이 억제용 약학 조성물\n\n  2)  출원일/  공개일/  출원번호: 2017. 1. 23./ 2018. 5. 17./ 제10-2017-0010370호\n\n  3)  청구범위2)\n\n   【청구항 1】육산화사비소(As4O6)를 포함하는(이하 '구성요소 1'이라 한다) 인간 상피\n\n세포성장인자 수용체-2(human epidermal growth factor receptor-2, HER-2)에 의해 매\n\n개되는 유방암 전이 억제용(이하 '구성요소 2'라 한다) 약학 조성물(이하 '이 사건 제1항 \n\n발명'이라 한다).\n\n      4)  주요  내용\n   배경기술  및  기술분야 \n    본  발명은  육산화사비소(As4O6)를  포함하는  암  전이  억제용  약학  조성물에  관한  것이다.  암 \n전이(cancer  metastasis)는  원발암(primary  tumor)  세포들이  다른  기관으로  퍼지는  현상으로, \n\n암의  마지막  단계라고  할  수  있다.  전이는  암  환자  사망  원인의  90%  이상을

In [14]:
from tkinter.filedialog import askopenfilename
from pdfminer.pdfdocument import PDFDocument
from pdfminer.pdfparser import PDFParser
from pdfminer.pdfinterp import PDFResourceManager, PDFPageInterpreter
from pdfminer.pdfdevice import PDFDevice, TagExtractor
from pdfminer.pdfpage import PDFPage
from pdfminer.converter import XMLConverter, HTMLConverter, TextConverter
from pdfminer.cmapdb import CMapDB
from pdfminer.layout import LAParams
from pdfminer.image import ImageWriter

In [ ]:
password = ''
pagenos = set()
maxpages = 0
# output option
outfile = None
outtype = None
imagewriter = None
rotation = 0
layoutmode = 'normal'
codec = 'utf-8'
codec = 'euc-kr'
pageno = 1
scale = 1
caching = True
showpageno = True
laparams = LAParams()

fpname = askopenfilename()
#fpname = "/home/hangyeol.sun/workspace/text.legal/pilot/pdf/2018허9015.pdf"
fp = open(fpname, 'rb')

outfpname = '/home/hangyeol.sun/workspace/text.legal/pilot/pdf2output'

rsrcmgr = PDFResourceManager(caching=caching)
outfp = file(outfpname + '.txt', 'w')
device = TextConverter(rsrcmgr, outfp, codec=codec, 
                       laparams=laparams, imagewriter=imagewriter)

interpreter = PDFPageInterpreter(rsrcmgr, device)
for page in PDFPage.get_pages(fp, pagenos,
                              maxpages=maxpages, password=password,
                              caching=caching, check_extractable=True):
    page.rotate = (page.rotate+rotation) % 360
    interpreter.process_page(page)
    
outfp.close()

rsrcmgr = PDFResourceManager(caching=caching)
outfp = file(outfpname + '.html', 'w')
device = HTMLConverter(rsrcmgr, outfp, codec=codec, scale=scale,
                       layoutmode=layoutmode, laparams=laparams,
                       imagewriter=imagewriter)

interpreter = PDFPageInterpreter(rsrcmgr, device)
for page in PDFPage.get_pages(fp, pagenos,
                              maxpages=maxpages, password=password,
                              caching=caching, check_extractable=True):
    page.rotate = (page.rotate+rotation) % 360
    interpreter.process_page(page)

outfp.close()

fp.close()